## Классификация текстовых данных. Реккурентные нейронные сети Many-To-One

In [108]:
import pandas as pd

data = pd.read_csv("../data/Petitions.csv")
data

id                               public_petition_text  \
0      3168490                                     снег на дороге   
1      3219678                очистить кабельный киоск от рекламы   
2      2963920  Просим убрать все деревья и кустарники, которы...   
3      3374910  Неудовлетворительное состояние парадной - надп...   
4      3336285                                           Граффити   
...        ...                                                ...   
59884  3128111                           прошу закрасить граффити   
59885  3276713       Прошу вас отремонтировать пешеходную дорожку   
59886  3274663  Необходимо демонтировать незаконную рекламную ...   
59887  3359308  Очень гремит на ветру металлическая часть окна...   
59888  3209098  Две проблемы в одном:\n1) Незаконные надписи/о...   

                                         reason_category  
0                                        Благоустройство  
1                                        Благоустройство  
2                                        Благоустройство  
3                                         Содержание МКД  
4                                        Благоустройство  
...                                                  ...  
59884                                    Благоустройство  
59885                                    Благоустройство  
59886  Незаконная информационная и (или) рекламная ко...  
59887                                             Кровля  
59888                                    Благоустройство  

[59889 rows x 3 columns]

In [109]:
corpus = data.drop(columns='id')[:20_000]
corpus

public_petition_text  reason_category
0                                         снег на дороге  Благоустройство
1                    очистить кабельный киоск от рекламы  Благоустройство
2      Просим убрать все деревья и кустарники, которы...  Благоустройство
3      Неудовлетворительное состояние парадной - надп...   Содержание МКД
4                                               Граффити  Благоустройство
...                                                  ...              ...
19995  реклама на водосточной трубе со стороны набере...  Благоустройство
19996                           снег не убран с асфальта  Благоустройство
19997  Резкий запах канализации с вентиляции, постоян...    Водоотведение
19998  18 января 2021 года обращался в Жкс 2 с пробле...   Содержание МКД
19999                                Не убирается мусор!  Благоустройство

[20000 rows x 2 columns]

### Предварительная обработка текстов корпуса

In [110]:
import re
texts_to_process = corpus['public_petition_text']

In [111]:
[text for text in texts_to_process]

['снег на дороге',
 'очистить кабельный киоск от рекламы',
 'Просим убрать все деревья и кустарники, которые вышли за пределы газона на пешеходную зону, начиная от подъезда №13 до подъезда №15 (фасад дома со стороны ул. Наличной).',
 'Неудовлетворительное состояние парадной - надписи на двери 2 этажа',
 'Граффити',
 'Необходимо проверить законность установки вывески на фасаде МКД по адресу проспект Непокорённых 74. В случае, если вывеска установлена незаконно её необходимо демонтировать',
 'Уборка не производится, на лестнице очень грязно. На всех этажах, вплоть до 5-го.\r\nЗвонок в ЖКС#2 5.04.2021 не дал результатов.',
 'Мусор',
 'Отсутствует освещение на лестничной площадке между 6 и 7 этажами в парадной № 2',
 'Зачем было делать благоустройство, если никто не убирает мусор??? И так ежедневно!',
 'Просьба закрасить',
 'Реклама на заборе.',
 'Снег с тротуаре не убран',
 'Проблема с регулярным вывозом мусора',
 'Рисунки',
 'Пожалуйста, удалите бетонный обрубок с ржавой арматурой с газо

*Удаление спец символов*

In [112]:
no_spec_symb_texts = [re.sub('[\n\r]*\n', '', text) for text in texts_to_process]
no_spec_symb_texts

['снег на дороге',
 'очистить кабельный киоск от рекламы',
 'Просим убрать все деревья и кустарники, которые вышли за пределы газона на пешеходную зону, начиная от подъезда №13 до подъезда №15 (фасад дома со стороны ул. Наличной).',
 'Неудовлетворительное состояние парадной - надписи на двери 2 этажа',
 'Граффити',
 'Необходимо проверить законность установки вывески на фасаде МКД по адресу проспект Непокорённых 74. В случае, если вывеска установлена незаконно её необходимо демонтировать',
 'Уборка не производится, на лестнице очень грязно. На всех этажах, вплоть до 5-го.Звонок в ЖКС#2 5.04.2021 не дал результатов.',
 'Мусор',
 'Отсутствует освещение на лестничной площадке между 6 и 7 этажами в парадной № 2',
 'Зачем было делать благоустройство, если никто не убирает мусор??? И так ежедневно!',
 'Просьба закрасить',
 'Реклама на заборе.',
 'Снег с тротуаре не убран',
 'Проблема с регулярным вывозом мусора',
 'Рисунки',
 'Пожалуйста, удалите бетонный обрубок с ржавой арматурой с газона п

*Токенизация*

In [113]:
from nltk.tokenize import sent_tokenize, word_tokenize  

In [114]:
[text for text in no_spec_symb_texts]

['снег на дороге',
 'очистить кабельный киоск от рекламы',
 'Просим убрать все деревья и кустарники, которые вышли за пределы газона на пешеходную зону, начиная от подъезда №13 до подъезда №15 (фасад дома со стороны ул. Наличной).',
 'Неудовлетворительное состояние парадной - надписи на двери 2 этажа',
 'Граффити',
 'Необходимо проверить законность установки вывески на фасаде МКД по адресу проспект Непокорённых 74. В случае, если вывеска установлена незаконно её необходимо демонтировать',
 'Уборка не производится, на лестнице очень грязно. На всех этажах, вплоть до 5-го.Звонок в ЖКС#2 5.04.2021 не дал результатов.',
 'Мусор',
 'Отсутствует освещение на лестничной площадке между 6 и 7 этажами в парадной № 2',
 'Зачем было делать благоустройство, если никто не убирает мусор??? И так ежедневно!',
 'Просьба закрасить',
 'Реклама на заборе.',
 'Снег с тротуаре не убран',
 'Проблема с регулярным вывозом мусора',
 'Рисунки',
 'Пожалуйста, удалите бетонный обрубок с ржавой арматурой с газона п

In [115]:
def nested_to_list(texts, f):
    list = []
    for text in texts:
        sentences = f(text)
        if len(sentences) > 1:
            for sentence in sentences: list.append(sentence)
        else: list.append(sentences[0])

    return  list

In [116]:
# texts_into_sentences = nested_to_list(no_spec_symb_texts, sent_tokenize)
texts_into_sentences = [sent_tokenize(text) for text in no_spec_symb_texts]
    
texts_into_sentences

[['снег на дороге'],
 ['очистить кабельный киоск от рекламы'],
 ['Просим убрать все деревья и кустарники, которые вышли за пределы газона на пешеходную зону, начиная от подъезда №13 до подъезда №15 (фасад дома со стороны ул.',
  'Наличной).'],
 ['Неудовлетворительное состояние парадной - надписи на двери 2 этажа'],
 ['Граффити'],
 ['Необходимо проверить законность установки вывески на фасаде МКД по адресу проспект Непокорённых 74.',
  'В случае, если вывеска установлена незаконно её необходимо демонтировать'],
 ['Уборка не производится, на лестнице очень грязно.',
  'На всех этажах, вплоть до 5-го.Звонок в ЖКС#2 5.04.2021 не дал результатов.'],
 ['Мусор'],
 ['Отсутствует освещение на лестничной площадке между 6 и 7 этажами в парадной № 2'],
 ['Зачем было делать благоустройство, если никто не убирает мусор???',
  'И так ежедневно!'],
 ['Просьба закрасить'],
 ['Реклама на заборе.'],
 ['Снег с тротуаре не убран'],
 ['Проблема с регулярным вывозом мусора'],
 ['Рисунки'],
 ['Пожалуйста, уда

In [117]:
tokens = [[word_tokenize(word) for word in text][0] for text in texts_into_sentences]
tokens

[['снег', 'на', 'дороге'],
 ['очистить', 'кабельный', 'киоск', 'от', 'рекламы'],
 ['Просим',
  'убрать',
  'все',
  'деревья',
  'и',
  'кустарники',
  ',',
  'которые',
  'вышли',
  'за',
  'пределы',
  'газона',
  'на',
  'пешеходную',
  'зону',
  ',',
  'начиная',
  'от',
  'подъезда',
  '№13',
  'до',
  'подъезда',
  '№15',
  '(',
  'фасад',
  'дома',
  'со',
  'стороны',
  'ул',
  '.'],
 ['Неудовлетворительное',
  'состояние',
  'парадной',
  '-',
  'надписи',
  'на',
  'двери',
  '2',
  'этажа'],
 ['Граффити'],
 ['Необходимо',
  'проверить',
  'законность',
  'установки',
  'вывески',
  'на',
  'фасаде',
  'МКД',
  'по',
  'адресу',
  'проспект',
  'Непокорённых',
  '74',
  '.'],
 ['Уборка',
  'не',
  'производится',
  ',',
  'на',
  'лестнице',
  'очень',
  'грязно',
  '.'],
 ['Мусор'],
 ['Отсутствует',
  'освещение',
  'на',
  'лестничной',
  'площадке',
  'между',
  '6',
  'и',
  '7',
  'этажами',
  'в',
  'парадной',
  '№',
  '2'],
 ['Зачем',
  'было',
  'делать',
  'благоуст

*Нормализация токенов (лемматизация)* 

In [118]:
from pymorphy3 import MorphAnalyzer
morph = MorphAnalyzer()

In [119]:
lemmas = [[morph.normal_forms(token)[0] for token in sentence] for sentence in tokens]
lemmas

[['снег', 'на', 'дорога'],
 ['очистить', 'кабельный', 'киоск', 'от', 'реклама'],
 ['просить',
  'убрать',
  'всё',
  'дерево',
  'и',
  'кустарник',
  ',',
  'который',
  'выйти',
  'за',
  'предел',
  'газон',
  'на',
  'пешеходный',
  'зона',
  ',',
  'начинать',
  'от',
  'подъезд',
  '№13',
  'до',
  'подъезд',
  '№15',
  '(',
  'фасад',
  'дом',
  'с',
  'сторона',
  'ул',
  '.'],
 ['неудовлетворительный',
  'состояние',
  'парадный',
  '-',
  'надпись',
  'на',
  'дверь',
  '2',
  'этаж'],
 ['граффити'],
 ['необходимо',
  'проверить',
  'законность',
  'установка',
  'вывеска',
  'на',
  'фасад',
  'мкд',
  'по',
  'адрес',
  'проспект',
  'непокорённый',
  '74',
  '.'],
 ['уборка',
  'не',
  'производиться',
  ',',
  'на',
  'лестница',
  'очень',
  'грязно',
  '.'],
 ['мусор'],
 ['отсутствовать',
  'освещение',
  'на',
  'лестничный',
  'площадка',
  'между',
  '6',
  'и',
  '7',
  'этаж',
  'в',
  'парадный',
  '№',
  '2'],
 ['зачем',
  'быть',
  'делать',
  'благоустройство',

In [120]:
def count_elements(nested):
    return sum(len([token for token in text]) for text in nested)

In [121]:
from string import punctuation
prepared_lemmas = [[lemma for lemma in sentence if lemma not in punctuation] for sentence in lemmas]
prepared_lemmas

[['снег', 'на', 'дорога'],
 ['очистить', 'кабельный', 'киоск', 'от', 'реклама'],
 ['просить',
  'убрать',
  'всё',
  'дерево',
  'и',
  'кустарник',
  'который',
  'выйти',
  'за',
  'предел',
  'газон',
  'на',
  'пешеходный',
  'зона',
  'начинать',
  'от',
  'подъезд',
  '№13',
  'до',
  'подъезд',
  '№15',
  'фасад',
  'дом',
  'с',
  'сторона',
  'ул'],
 ['неудовлетворительный',
  'состояние',
  'парадный',
  'надпись',
  'на',
  'дверь',
  '2',
  'этаж'],
 ['граффити'],
 ['необходимо',
  'проверить',
  'законность',
  'установка',
  'вывеска',
  'на',
  'фасад',
  'мкд',
  'по',
  'адрес',
  'проспект',
  'непокорённый',
  '74'],
 ['уборка', 'не', 'производиться', 'на', 'лестница', 'очень', 'грязно'],
 ['мусор'],
 ['отсутствовать',
  'освещение',
  'на',
  'лестничный',
  'площадка',
  'между',
  '6',
  'и',
  '7',
  'этаж',
  'в',
  'парадный',
  '№',
  '2'],
 ['зачем',
  'быть',
  'делать',
  'благоустройство',
  'если',
  'никто',
  'не',
  'убирать',
  'мусор'],
 ['просьба', 

In [122]:
def before_after(before: str, after: str):
    print(f'До удаления: {count_elements(before)}')
    print(f'После удаления: {count_elements(after)}')

In [123]:
print(f'До удаления спец символов: {count_elements(lemmas)}')
print(f'После удаления спец символов: {count_elements(prepared_lemmas)}')

До удаления спец символов: 173018
После удаления спец символов: 151267


*Удаление стоп-слов*

In [124]:
from nltk.corpus import stopwords
stopwords = stopwords.words('russian')

In [125]:
prepared_tokens = [[token for token in text if token not in stopwords] for text in prepared_lemmas]
before_after(prepared_lemmas, prepared_tokens)

До удаления: 151267
После удаления: 118538


In [126]:
prepared_tokens

[['снег', 'дорога'],
 ['очистить', 'кабельный', 'киоск', 'реклама'],
 ['просить',
  'убрать',
  'всё',
  'дерево',
  'кустарник',
  'который',
  'выйти',
  'предел',
  'газон',
  'пешеходный',
  'зона',
  'начинать',
  'подъезд',
  '№13',
  'подъезд',
  '№15',
  'фасад',
  'дом',
  'сторона',
  'ул'],
 ['неудовлетворительный',
  'состояние',
  'парадный',
  'надпись',
  'дверь',
  '2',
  'этаж'],
 ['граффити'],
 ['необходимо',
  'проверить',
  'законность',
  'установка',
  'вывеска',
  'фасад',
  'мкд',
  'адрес',
  'проспект',
  'непокорённый',
  '74'],
 ['уборка', 'производиться', 'лестница', 'очень', 'грязно'],
 ['мусор'],
 ['отсутствовать',
  'освещение',
  'лестничный',
  'площадка',
  '6',
  '7',
  'этаж',
  'парадный',
  '№',
  '2'],
 ['делать', 'благоустройство', 'никто', 'убирать', 'мусор'],
 ['просьба', 'закрасить'],
 ['реклама', 'забор'],
 ['снег', 'тротуар', 'убрать'],
 ['проблема', 'регулярный', 'вывоз', 'мусор'],
 ['рисунок'],
 ['пожалуйста',
  'удалить',
  'бетонный',
 

--------------------------------------------------
(Для исключения необходимости предобрабатывать заново):

In [127]:
import pickle

with open('../data/petitions_preprocessed_tokens', 'wb') as f:
    pickle.dump(prepared_tokens, f)


In [128]:
import pickle

with open('../data/petitions_preprocessed_tokens', 'rb') as f:
    prepared_tokens_imported = pickle.load(f)


---------------------------------------------------

In [129]:
from gensim.models import Word2Vec

In [130]:
w2v = Word2Vec(sentences=prepared_tokens, min_count=2, vector_size=64, epochs=50)

In [131]:
w2v.wv['снег'], w2v.wv['снег'].shape

(array([-2.7067077 ,  0.8230923 , -0.19296664,  0.75407654,  0.00631162,
         0.6400961 ,  1.6797737 , -0.3189055 ,  1.0693733 , -3.695857  ,
        -1.6713799 ,  2.9955254 , -0.17033286,  0.29248473, -0.6589577 ,
         0.696359  , -2.2400966 , -0.69927907,  1.4364918 ,  0.9260128 ,
         0.10188256, -1.34033   ,  1.7538142 , -2.3605418 ,  1.2392881 ,
        -0.63490033, -0.95812213,  0.69351405, -0.15869278, -1.0371904 ,
        -0.26002416, -0.38047087, -0.81954455, -2.5470746 ,  2.456511  ,
        -2.0213833 ,  1.4711274 ,  1.0601395 , -0.36373502, -1.1895337 ,
         3.562246  ,  0.47862616,  0.02919896, -0.23167165,  0.8740734 ,
        -3.1783905 ,  2.592874  , -1.698537  ,  1.2280282 , -0.05539207,
         1.1582631 , -0.08613474, -1.1123464 ,  1.4017135 , -1.5483446 ,
         1.1116269 ,  0.5018321 , -0.38374147, -0.90289694,  2.1207144 ,
        -2.0647435 , -2.7333603 , -0.6215287 , -1.7144744 ], dtype=float32),
 (64,))

*Кодирование признака обращения*

In [132]:
w2v.wv.most_similar('подъезд', topn=3)

[('парадный', 0.8898110389709473),
 ('тамбур', 0.599067747592926),
 ('этаж', 0.5379970669746399)]

In [133]:
import numpy as np

Опытным путём было выявлены сложности работы с векторовидной меткой `reason_category`, потому применим обычное порядковое кодирование:

In [134]:
# corpus['reason_category']

In [135]:
unique_categories = corpus['reason_category'].unique().tolist()

mapping_dict = {unique_categories[i]: i for i in range(len(unique_categories))}
mapping_dict

{'Благоустройство': 0,
 'Содержание МКД': 1,
 'Незаконная информационная и (или) рекламная конструкция': 2,
 'Фасад': 3,
 'Водоснабжение': 4,
 'Нарушение правил пользования общим имуществом': 5,
 'Повреждения или неисправность элементов уличной инфраструктуры': 6,
 'Кровля': 7,
 'Состояние рекламных или информационных конструкций': 8,
 'Нарушение порядка пользования общим имуществом': 9,
 'Подвалы': 10,
 'Водоотведение': 11,
 'Санитарное состояние': 12,
 'Центральное отопление': 13,
 'Незаконная реализация товаров с торгового оборудования (прилавок, ящик, с земли)': 14}

In [136]:
# unique_categories = corpus['reason_category'].unique().tolist()
# eye = np.eye(len(unique_categories))

# # for row in eye:
# dict = {unique_categories[i]: eye[i] for i in range(len(unique_categories))}
# dict

In [137]:
corpus['reason_category_encoded'] = corpus['reason_category'].map(mapping_dict)
corpus

public_petition_text  reason_category  \
0                                         снег на дороге  Благоустройство   
1                    очистить кабельный киоск от рекламы  Благоустройство   
2      Просим убрать все деревья и кустарники, которы...  Благоустройство   
3      Неудовлетворительное состояние парадной - надп...   Содержание МКД   
4                                               Граффити  Благоустройство   
...                                                  ...              ...   
19995  реклама на водосточной трубе со стороны набере...  Благоустройство   
19996                           снег не убран с асфальта  Благоустройство   
19997  Резкий запах канализации с вентиляции, постоян...    Водоотведение   
19998  18 января 2021 года обращался в Жкс 2 с пробле...   Содержание МКД   
19999                                Не убирается мусор!  Благоустройство   

       reason_category_encoded  
0                            0  
1                            0  
2                            0  
3                            1  
4                            0  
...                        ...  
19995                        0  
19996                        0  
19997                       11  
19998                        1  
19999                        0  

[20000 rows x 3 columns]

In [138]:
w2v.wv.vectors

array([[-0.01350709, -0.94718766, -0.23868193, ...,  0.28795242,
         0.0437858 , -2.9490445 ],
       [-2.1759398 ,  0.25137982,  1.6542656 , ...,  0.2624626 ,
        -0.28980115,  0.00899341],
       [ 0.36944416,  2.2736168 ,  1.0969605 , ..., -0.307278  ,
        -0.54203254,  0.9113098 ],
       ...,
       [-0.03102195, -0.43549922,  0.26629323, ..., -0.3841856 ,
         0.1384339 , -0.07976032],
       [ 0.0857743 , -0.43761563,  0.06779681, ...,  0.24819992,
        -0.04033566, -0.23454653],
       [ 0.03104092,  0.26732937, -0.00876065, ..., -0.14977165,
         0.17939302,  0.0550308 ]], dtype=float32)

In [139]:
corpus.loc[0]

public_petition_text        снег на дороге
reason_category            Благоустройство
reason_category_encoded                  0
Name: 0, dtype: object

In [140]:
delete_indexes = []
prepared_tokens_chosen = [] 

for i in range(len(prepared_tokens)):
    if len(prepared_tokens[i]) == 1:
        delete_indexes.append(i)
        continue
    prepared_tokens_chosen.append(prepared_tokens[i])
    # for j in range(len(prepared_tokens[i])):
        # prepared_tokens_chosen[i][j] = prepared_tokens[i][j]

In [141]:
before_after(prepared_tokens, prepared_tokens_chosen)

До удаления: 118538
После удаления: 116956


In [142]:
for text in prepared_tokens_chosen:
    for word in text:
        if word =='ланский': print(text)

['ланский', 'шоссе', 'д12к1', 'парадный', '4повредить', 'почтовый', 'ящик', 'просить', 'заменить']


In [143]:
for text in prepared_tokens_chosen:
    for word in text:
        print(word)

снег
дорога
очистить
кабельный
киоск
реклама
просить
убрать
всё
дерево
кустарник
который
выйти
предел
газон
пешеходный
зона
начинать
подъезд
№13
подъезд
№15
фасад
дом
сторона
ул
неудовлетворительный
состояние
парадный
надпись
дверь
2
этаж
необходимо
проверить
законность
установка
вывеска
фасад
мкд
адрес
проспект
непокорённый
74
уборка
производиться
лестница
очень
грязно
отсутствовать
освещение
лестничный
площадка
6
7
этаж
парадный
№
2
делать
благоустройство
никто
убирать
мусор
просьба
закрасить
реклама
забор
снег
тротуар
убрать
проблема
регулярный
вывоз
мусор
пожалуйста
удалить
бетонный
обрубка
ржавый
арматура
газон
дом
мусор
асфальт
ланский
шоссе
д12к1
парадный
4повредить
почтовый
ящик
просить
заменить
кривой
висеть
просьба
поправить
3
подьезд
1
этаж
плохой
уборка
улица
надпись
забор
частично
разрушить
ограждение
контейнерный
площадка
демонтаж
рекламный
вывеска
фасад
образоваться
повреждения.требоваться
произвести
работа
качественный
восстановление
штукатурно-окрасочный
слой
соответст

In [144]:
w2v.wv

In [145]:
prepared_tokens_vectorized = [[] for _ in prepared_tokens_chosen]

for i in range(len(prepared_tokens_chosen)):
    for j in range(len(prepared_tokens_chosen[i])):
        try: 
            prepared_tokens_vectorized[i].append(w2v.wv[prepared_tokens_chosen[i][j]])
        except: 
            ...
            

In [146]:
corpus

public_petition_text  reason_category  \
0                                         снег на дороге  Благоустройство   
1                    очистить кабельный киоск от рекламы  Благоустройство   
2      Просим убрать все деревья и кустарники, которы...  Благоустройство   
3      Неудовлетворительное состояние парадной - надп...   Содержание МКД   
4                                               Граффити  Благоустройство   
...                                                  ...              ...   
19995  реклама на водосточной трубе со стороны набере...  Благоустройство   
19996                           снег не убран с асфальта  Благоустройство   
19997  Резкий запах канализации с вентиляции, постоян...    Водоотведение   
19998  18 января 2021 года обращался в Жкс 2 с пробле...   Содержание МКД   
19999                                Не убирается мусор!  Благоустройство   

       reason_category_encoded  
0                            0  
1                            0  
2                            0  
3                            1  
4                            0  
...                        ...  
19995                        0  
19996                        0  
19997                       11  
19998                        1  
19999                        0  

[20000 rows x 3 columns]

In [147]:
corpus_filtered = corpus.drop(delete_indexes)
corpus_filtered.reset_index(inplace=True, drop=True)
corpus_filtered

public_petition_text  \
0                                         снег на дороге   
1                    очистить кабельный киоск от рекламы   
2      Просим убрать все деревья и кустарники, которы...   
3      Неудовлетворительное состояние парадной - надп...   
4      Необходимо проверить законность установки выве...   
...                                                  ...   
18413  реклама на водосточной трубе со стороны набере...   
18414                           снег не убран с асфальта   
18415  Резкий запах канализации с вентиляции, постоян...   
18416  18 января 2021 года обращался в Жкс 2 с пробле...   
18417                                Не убирается мусор!   

                                         reason_category  \
0                                        Благоустройство   
1                                        Благоустройство   
2                                        Благоустройство   
3                                         Содержание МКД   
4      Незаконная информационная и (или) рекламная ко...   
...                                                  ...   
18413                                    Благоустройство   
18414                                    Благоустройство   
18415                                      Водоотведение   
18416                                     Содержание МКД   
18417                                    Благоустройство   

       reason_category_encoded  
0                            0  
1                            0  
2                            0  
3                            1  
4                            2  
...                        ...  
18413                        0  
18414                        0  
18415                       11  
18416                        1  
18417                        0  

[18418 rows x 3 columns]

In [148]:
corpus_filtered['public_petition_vectors'] = prepared_tokens_vectorized
corpus_filtered

public_petition_text  \
0                                         снег на дороге   
1                    очистить кабельный киоск от рекламы   
2      Просим убрать все деревья и кустарники, которы...   
3      Неудовлетворительное состояние парадной - надп...   
4      Необходимо проверить законность установки выве...   
...                                                  ...   
18413  реклама на водосточной трубе со стороны набере...   
18414                           снег не убран с асфальта   
18415  Резкий запах канализации с вентиляции, постоян...   
18416  18 января 2021 года обращался в Жкс 2 с пробле...   
18417                                Не убирается мусор!   

                                         reason_category  \
0                                        Благоустройство   
1                                        Благоустройство   
2                                        Благоустройство   
3                                         Содержание МКД   
4      Незаконная информационная и (или) рекламная ко...   
...                                                  ...   
18413                                    Благоустройство   
18414                                    Благоустройство   
18415                                      Водоотведение   
18416                                     Содержание МКД   
18417                                    Благоустройство   

       reason_category_encoded  \
0                            0   
1                            0   
2                            0   
3                            1   
4                            2   
...                        ...   
18413                        0   
18414                        0   
18415                       11   
18416                        1   
18417                        0   

                                 public_petition_vectors  
0      [[-2.7067077, 0.8230923, -0.19296664, 0.754076...  
1      [[1.7452637, 1.1509963, 2.8950167, 2.5716565, ...  
2      [[0.5546885, -0.8326027, 1.1503941, -0.1927245...  
3      [[2.1304874, 2.642467, 2.0697536, -3.518034, -...  
4      [[1.2932223, -0.10673804, -0.08491588, -0.5993...  
...                                                  ...  
18413  [[1.2092762, 0.010634458, 1.3782363, 1.3131081...  
18414  [[-2.7067077, 0.8230923, -0.19296664, 0.754076...  
18415  [[-0.095715545, -0.079312176, -0.23618846, 0.2...  
18416  [[0.19524004, -0.23240069, -0.5712172, -3.5966...  
18417  [[0.14636509, -0.8076624, 0.12862216, 0.768830...  

[18418 rows x 4 columns]

In [149]:
import pickle

with open('../data/petitions_vectorized_and_coded', 'wb') as f:
    pickle.dump(corpus_filtered, f)

In [150]:
import pickle

with open('../data/petitions_vectorized_and_coded', 'rb') as f:
    corpus_imported = pickle.load(f)

corpus_imported

public_petition_text  \
0                                         снег на дороге   
1                    очистить кабельный киоск от рекламы   
2      Просим убрать все деревья и кустарники, которы...   
3      Неудовлетворительное состояние парадной - надп...   
4      Необходимо проверить законность установки выве...   
...                                                  ...   
18413  реклама на водосточной трубе со стороны набере...   
18414                           снег не убран с асфальта   
18415  Резкий запах канализации с вентиляции, постоян...   
18416  18 января 2021 года обращался в Жкс 2 с пробле...   
18417                                Не убирается мусор!   

                                         reason_category  \
0                                        Благоустройство   
1                                        Благоустройство   
2                                        Благоустройство   
3                                         Содержание МКД   
4      Незаконная информационная и (или) рекламная ко...   
...                                                  ...   
18413                                    Благоустройство   
18414                                    Благоустройство   
18415                                      Водоотведение   
18416                                     Содержание МКД   
18417                                    Благоустройство   

       reason_category_encoded  \
0                            0   
1                            0   
2                            0   
3                            1   
4                            2   
...                        ...   
18413                        0   
18414                        0   
18415                       11   
18416                        1   
18417                        0   

                                 public_petition_vectors  
0      [[-2.7067077, 0.8230923, -0.19296664, 0.754076...  
1      [[1.7452637, 1.1509963, 2.8950167, 2.5716565, ...  
2      [[0.5546885, -0.8326027, 1.1503941, -0.1927245...  
3      [[2.1304874, 2.642467, 2.0697536, -3.518034, -...  
4      [[1.2932223, -0.10673804, -0.08491588, -0.5993...  
...                                                  ...  
18413  [[1.2092762, 0.010634458, 1.3782363, 1.3131081...  
18414  [[-2.7067077, 0.8230923, -0.19296664, 0.754076...  
18415  [[-0.095715545, -0.079312176, -0.23618846, 0.2...  
18416  [[0.19524004, -0.23240069, -0.5712172, -3.5966...  
18417  [[0.14636509, -0.8076624, 0.12862216, 0.768830...  

[18418 rows x 4 columns]

In [151]:
import numpy as np

np.array(corpus_imported['public_petition_vectors'][0]).shape

(2, 64)

In [152]:
empty_ids = []
for i, seq in enumerate(corpus_imported['public_petition_vectors']):    
    if len(seq) == 0: empty_ids.append(i)

corpus_imported = corpus_imported.drop(empty_ids)
corpus_imported.reset_index(inplace=True, drop=True)
corpus_imported

public_petition_text  \
0                                         снег на дороге   
1                    очистить кабельный киоск от рекламы   
2      Просим убрать все деревья и кустарники, которы...   
3      Неудовлетворительное состояние парадной - надп...   
4      Необходимо проверить законность установки выве...   
...                                                  ...   
18409  реклама на водосточной трубе со стороны набере...   
18410                           снег не убран с асфальта   
18411  Резкий запах канализации с вентиляции, постоян...   
18412  18 января 2021 года обращался в Жкс 2 с пробле...   
18413                                Не убирается мусор!   

                                         reason_category  \
0                                        Благоустройство   
1                                        Благоустройство   
2                                        Благоустройство   
3                                         Содержание МКД   
4      Незаконная информационная и (или) рекламная ко...   
...                                                  ...   
18409                                    Благоустройство   
18410                                    Благоустройство   
18411                                      Водоотведение   
18412                                     Содержание МКД   
18413                                    Благоустройство   

       reason_category_encoded  \
0                            0   
1                            0   
2                            0   
3                            1   
4                            2   
...                        ...   
18409                        0   
18410                        0   
18411                       11   
18412                        1   
18413                        0   

                                 public_petition_vectors  
0      [[-2.7067077, 0.8230923, -0.19296664, 0.754076...  
1      [[1.7452637, 1.1509963, 2.8950167, 2.5716565, ...  
2      [[0.5546885, -0.8326027, 1.1503941, -0.1927245...  
3      [[2.1304874, 2.642467, 2.0697536, -3.518034, -...  
4      [[1.2932223, -0.10673804, -0.08491588, -0.5993...  
...                                                  ...  
18409  [[1.2092762, 0.010634458, 1.3782363, 1.3131081...  
18410  [[-2.7067077, 0.8230923, -0.19296664, 0.754076...  
18411  [[-0.095715545, -0.079312176, -0.23618846, 0.2...  
18412  [[0.19524004, -0.23240069, -0.5712172, -3.5966...  
18413  [[0.14636509, -0.8076624, 0.12862216, 0.768830...  

[18414 rows x 4 columns]

In [153]:
from torch import nn
import torch

from torch.utils.data import DataLoader, Dataset

In [154]:
X = corpus_imported['public_petition_vectors']
y = corpus_imported['reason_category_encoded']

X = [torch.tensor(row) for row in X]


In [155]:
print(X[0].shape, X[0])
print(y[0].shape)

torch.Size([2, 64]) tensor([[-2.7067,  0.8231, -0.1930,  0.7541,  0.0063,  0.6401,  1.6798, -0.3189,
          1.0694, -3.6959, -1.6714,  2.9955, -0.1703,  0.2925, -0.6590,  0.6964,
         -2.2401, -0.6993,  1.4365,  0.9260,  0.1019, -1.3403,  1.7538, -2.3605,
          1.2393, -0.6349, -0.9581,  0.6935, -0.1587, -1.0372, -0.2600, -0.3805,
         -0.8195, -2.5471,  2.4565, -2.0214,  1.4711,  1.0601, -0.3637, -1.1895,
          3.5622,  0.4786,  0.0292, -0.2317,  0.8741, -3.1784,  2.5929, -1.6985,
          1.2280, -0.0554,  1.1583, -0.0861, -1.1123,  1.4017, -1.5483,  1.1116,
          0.5018, -0.3837, -0.9029,  2.1207, -2.0647, -2.7334, -0.6215, -1.7145],
        [-0.7202,  0.6131,  0.4312, -0.8630,  0.4296,  0.6452,  1.0247,  1.3300,
         -0.3816, -1.0940, -0.0866,  0.8009,  0.0049,  0.2859, -0.5616,  0.2735,
          0.2436, -1.7763, -1.8065,  0.9148,  0.2148, -0.1594,  0.3322, -0.1321,
         -1.8209,  1.6523,  1.8245,  1.3993,  0.3333, -1.5051,  1.0368,  0.4949,
       

In [156]:
import torch
import torch.nn as nn
import torch.optim 
from torch.utils.data import DataLoader, TensorDataset
import numpy as np

from sklearn.model_selection import train_test_split

In [157]:
from torch.nn.utils.rnn import pad_sequence


X_padded = pad_sequence(X, batch_first=True) 

y.values.reshape(-1, 1)

X_train, X_test, y_train, y_test = train_test_split(X_padded, y.values, test_size= .2) 

In [158]:
print(X_padded[2].shape, X[2])
print(y[0].shape)

torch.Size([102, 64]) tensor([[ 0.5547, -0.8326,  1.1504,  ..., -0.7502,  0.0624, -1.2532],
        [-0.2111,  0.4600,  2.0048,  ..., -0.9384, -0.8160,  0.2561],
        [-0.7239,  0.3448, -1.1764,  ..., -2.2121,  0.4338, -3.6637],
        ...,
        [-2.1759,  0.2514,  1.6543,  ...,  0.2625, -0.2898,  0.0090],
        [-0.6884, -1.8499,  1.9865,  ..., -1.1687, -0.4723, -0.3173],
        [ 0.3639,  0.4244, -0.8520,  ...,  0.2164,  3.0247,  1.0266]])
()


In [159]:
X_train_tensor = torch.tensor(X_train, dtype=torch.float32, device='cuda:0')
X_test_tensor = torch.tensor(X_test, dtype=torch.float32, device='cuda:0')
y_test_tensor = torch.tensor(y_test, dtype=torch.long, device='cuda:0')
y_train_tensor = torch.tensor(y_train, dtype=torch.long, device='cuda:0')


C:\Users\gunte\AppData\Local\Temp\ipykernel_23204\2320602126.py:1: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  X_train_tensor = torch.tensor(X_train, dtype=torch.float32, device='cuda:0')
C:\Users\gunte\AppData\Local\Temp\ipykernel_23204\2320602126.py:2: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  X_test_tensor = torch.tensor(X_test, dtype=torch.float32, device='cuda:0')


In [160]:
X_train_tensor.shape, y_train_tensor.shape

(torch.Size([14731, 102, 64]), torch.Size([14731]))

In [161]:
train_ds = TensorDataset(X_train_tensor, y_train_tensor)
train_dl = DataLoader(train_ds, batch_size=64, shuffle=True)

test_ds = TensorDataset(X_test_tensor, y_test_tensor)
test_dl = DataLoader(test_ds, batch_size=64, shuffle=False)

### RNN

In [162]:
class SimpleRNN(nn.Module):
    def __init__(self, input_size, hidden_size, output_size):
        super(SimpleRNN, self).__init__()
        self.hidden_size = hidden_size
        self.rnn = nn.RNN(input_size, hidden_size, batch_first=True)
        self.linear = nn.Linear(hidden_size, output_size)

    def forward(self, x):
        h0 = torch.zeros(1, x.size(0), self.hidden_size).to(x.device)
        out, _ = self.rnn(x, h0)
        out = self.linear(out[:, -1, :])
        return out
        



In [163]:
input_size = X_test_tensor.shape[-1] # batch size
hidden_size = 256
output_size = len(set(corpus_imported['reason_category_encoded']))

In [164]:
model = SimpleRNN(input_size, hidden_size, output_size)
model.to(device='cuda:0')

SimpleRNN(
  (rnn): RNN(64, 256, batch_first=True)
  (linear): Linear(in_features=256, out_features=15, bias=True)
)

In [165]:
unique_reason_cat_coded = set(corpus_imported['reason_category_encoded'])

classes_count = []
for number in unique_reason_cat_coded:
    count = corpus_imported[corpus_imported['reason_category_encoded'] == number].count()['reason_category_encoded']
    classes_count.append(count)

class_weights = torch.tensor([1/num_samples for num_samples in classes_count], dtype=torch.float32).to('cuda:0')

In [166]:
class_weights

tensor([9.6302e-05, 2.1290e-04, 1.6667e-03, 2.0325e-03, 3.7313e-03, 1.7007e-03,
        2.6316e-03, 3.8168e-03, 5.3476e-03, 1.3158e-02, 1.3699e-02, 1.1765e-02,
        6.8966e-03, 1.0753e-02, 1.1905e-02], device='cuda:0')

In [167]:
loss = nn.CrossEntropyLoss(weight=class_weights)

optimizer = torch.optim.Adam(model.parameters(),  lr= .003)
epochs = 25

for epoch in range(epochs):
    total_loss = 0
    for x, y in train_dl:
        # прямое распространение - получаем предсказание
        outputs = model(x)

        # вычисляем значение функции потерь
        loss_value = loss(outputs, y)

        # вычисляются значения grad у слоёв модели
        loss_value.backward()

        # шаг градиентного спуска с заданным lr оптимизатора
        optimizer.step()

        # занулить градиент для вычисления его на новой итерации
        optimizer.zero_grad()

        total_loss += loss_value.item()
    
    
    print(f'Эпоха: {epoch + 1}, значение функции потерь: {total_loss/len(train_dl)}')




Эпоха: 1, значение функции потерь: 2.731059542982093
Эпоха: 2, значение функции потерь: 2.7221469554034146
Эпоха: 3, значение функции потерь: 2.7447861113073504
Эпоха: 4, значение функции потерь: 2.756083120515336
Эпоха: 5, значение функции потерь: 2.7546842789753176
Эпоха: 6, значение функции потерь: 2.77455717867071
Эпоха: 7, значение функции потерь: 2.7634807479329955
Эпоха: 8, значение функции потерь: 2.7804260212621648
Эпоха: 9, значение функции потерь: 2.7366450988885127
Эпоха: 10, значение функции потерь: 2.771231168276304
Эпоха: 11, значение функции потерь: 2.800848524291794
Эпоха: 12, значение функции потерь: 2.7736305916980233
Эпоха: 13, значение функции потерь: 2.722977436982192
Эпоха: 14, значение функции потерь: 2.766719016161832
Эпоха: 15, значение функции потерь: 2.711488321230009
Эпоха: 16, значение функции потерь: 2.749075558278468
Эпоха: 17, значение функции потерь: 2.748013886538419
Эпоха: 18, значение функции потерь: 2.7971594509108244
Эпоха: 19, значение функции по

In [168]:
def evaluate():
    '''
    This method is for EVALUATUION purposes.
    Returns: `y_true` and `y_pred`
    '''
    y_true = []
    y_pred = []

    with torch.no_grad():
        for x, y in test_dl:
            x, y = x.to('cuda:0'), y.to('cuda:0')
            outputs = model(x)
            _, predicted = torch.max(outputs, 1)
            print(y.cpu().numpy())
            print(predicted.cpu().numpy())
            print('-----------------')
            y_true.extend(y.cpu().numpy())
            y_pred.extend(predicted.cpu().numpy())
            
    return y_true, y_pred

In [169]:
from sklearn.metrics import classification_report
y_true, y_pred = evaluate()

print(classification_report(y_true, y_pred))

[ 0  1  0  1  0  0 14  0  0  1  0  1  0  1  1  1  0  0  5  0  3  0  6  1
  5  0 13  0  0  0  1  5  6  0  1  1  0  0  1  1  0  0  0  7  4  1  0  1
  3  0  0  1  1  0  0  1  0  5  2  0  0  0  4  1]
[2 6 2 2 2 6 6 2 6 6 6 6 2 2 6 6 2 6 6 2 6 6 6 6 6 6 6 2 6 6 6 2 6 6 2 6 2
 6 6 6 6 6 2 6 6 6 2 6 2 2 6 6 6 6 6 6 6 6 2 2 2 2 6 6]
-----------------
[ 0  0  3  1  0  0  1  3 13  1  0  0  0  1  0 11 13  0  1  0  0  0  0  0
  0  0  0  0  6  0  0  0  0  1  0  1  0  0  2 14  1  0  0  0  0  1  0  0
  0  0  0  0  0  0  0  0  1  1  0  0  0  0  0  0]
[2 6 6 6 2 6 2 6 6 6 6 6 2 2 2 6 6 6 6 6 2 2 6 6 6 6 6 2 6 2 6 6 2 6 2 2 6
 2 2 2 6 6 6 2 2 2 2 6 2 6 6 6 2 6 2 6 6 2 6 6 6 6 6 2]
-----------------
[ 0  0  1  0  0  0  0  0  0  0  1  0  0  0  7  1  0  1  0  1  0  0  0  6
  3  1  0  1  0  1  8  0  4  0  5  1  0  1  3 12  0  1  1  0  0 13  0  0
  0  0  0  0  1  0  1  0  0  0  1  0  0  4  1  1]
[2 6 6 6 6 2 6 6 6 2 6 6 6 2 6 6 2 2 6 6 2 6 2 6 6 6 6 6 6 6 6 6 6 6 6 6 6
 6 2 6 2 6 6 6 2 6 6 6 2 6 6 2 6 2 6 2 

c:\Users\gunte\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\Users\gunte\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\Users\gunte\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modif

### LSTM

In [170]:
class LSTM(nn.Module):
    def __init__(self, input_dim, hidden_dim, layer_dim, output_dim):
        super(LSTM, self).__init__()
        self.hidden_dim = hidden_dim
        self.layer_dim = layer_dim
        self.lstm = nn.LSTM(input_dim, hidden_dim, layer_dim, batch_first=True)
        self.linear = nn.Linear(hidden_dim, output_dim)

    def forward(self, x, h0, c0):
        # Forward pass через LSTM
        out, (hn, cn) = self.lstm(x, (h0, c0))
        out = self.linear(out[:, -1, :]) # Выбираем последний временной шаг
        return out, hn, cn

In [171]:
input_size = X_test_tensor.shape[-1] # batch size
output_size = len(set(corpus_imported['reason_category_encoded']))

In [172]:
model = LSTM(input_dim=input_size, hidden_dim=128, layer_dim=1, output_dim=output_size)
model.to(device='cuda:0')

LSTM(
  (lstm): LSTM(64, 128, batch_first=True)
  (linear): Linear(in_features=128, out_features=15, bias=True)
)

In [173]:
num_epochs = 30
loss = nn.CrossEntropyLoss(weight=class_weights)

optimizer = torch.optim.Adam(model.parameters(),  lr= .003)

h0 = torch.zeros(model.layer_dim, train_dl.batch_size, model.hidden_dim, device='cuda:0')
c0 = torch.zeros(model.layer_dim, train_dl.batch_size, model.hidden_dim, device='cuda:0')
for epoch in range(num_epochs):
    for batch_idx, (x, y) in enumerate(train_dl):
        model.train()
        optimizer.zero_grad()

        batch_size = x.size(0)
        if h0.size(1) != batch_size:
            h0 = torch.zeros(model.layer_dim, batch_size, model.hidden_dim, device='cuda:0')
            c0 = torch.zeros(model.layer_dim, batch_size, model.hidden_dim, device='cuda:0')

        # Forward pass
        outputs, h0, c0 = model(x, h0, c0)

            # Detach hidden states для предотвращения обратного распространения по всей последовательности
        h0 = h0.detach()
        c0 = c0.detach()

            # Compute loss
        loss_value = loss(outputs, y)
        loss_value.backward()
        optimizer.step()

    print(f'Epoch [{epoch+1}/{num_epochs}], Loss: {loss_value.item():.4f}')

Epoch [1/30], Loss: 2.7233
Epoch [2/30], Loss: 2.6891
Epoch [3/30], Loss: 2.7054
Epoch [4/30], Loss: 2.7694
Epoch [5/30], Loss: 2.6037
Epoch [6/30], Loss: 2.6733
Epoch [7/30], Loss: 2.6001
Epoch [8/30], Loss: 2.6543
Epoch [9/30], Loss: 2.6633
Epoch [10/30], Loss: 2.6712
Epoch [11/30], Loss: 2.6208
Epoch [12/30], Loss: 2.6089
Epoch [13/30], Loss: 2.6026
Epoch [14/30], Loss: 2.6311
Epoch [15/30], Loss: 2.5970
Epoch [16/30], Loss: 2.6454
Epoch [17/30], Loss: 2.8083
Epoch [18/30], Loss: 2.6213
Epoch [19/30], Loss: 2.6711
Epoch [20/30], Loss: 2.5969
Epoch [21/30], Loss: 2.5880
Epoch [22/30], Loss: 2.5965
Epoch [23/30], Loss: 2.7865
Epoch [24/30], Loss: 2.6288
Epoch [25/30], Loss: 2.8399
Epoch [26/30], Loss: 2.6761
Epoch [27/30], Loss: 2.8122
Epoch [28/30], Loss: 2.6052
Epoch [29/30], Loss: 1.7902
Epoch [30/30], Loss: 2.7067


### GRU

In [174]:
class SimpleGRU(nn.Module):
    def __init__(self, input_size, hidden_size, output_size, layers_number):
        super(SimpleGRU, self).__init__()
        self.hidden_size = hidden_size
        self.layers_number = layers_number
        # our layers:
        self.gru = nn.GRU(input_size, hidden_size, layers_number, batch_first=True)
        self.linear = nn.Linear(hidden_size, output_size)
    
    def forward(self, x):
        h0 = torch.zeros(self.layers_number, x.size(0), self.hidden_size).to(x.device)

        out, _ = self.gru(x, h0)
        out = out[:, -1, :]
        out = self.linear(out)

        return out


In [175]:
input_size = X_test_tensor.shape[-1] # batch size
output_size = len(set(corpus_imported['reason_category_encoded']))

gru_model = SimpleGRU(input_size, hidden_size=128, output_size=output_size, layers_number=1)
gru_model.to(device='cuda:0')

SimpleGRU(
  (gru): GRU(64, 128, batch_first=True)
  (linear): Linear(in_features=128, out_features=15, bias=True)
)

In [176]:
optimizer = torch.optim.Adam(gru_model.parameters(), lr=.004)
loss_function = nn.CrossEntropyLoss(weight=class_weights)

epochs = 30
for epoch in range(epochs):
    total_loss = 0
    for x, y in train_dl:
        # прямое распространение - получаем предсказание
        outputs = gru_model(x)

        # вычисляем значение функции потерь
        loss_value = loss_function(outputs, y)

        # вычисляются значения grad у слоёв модели
        loss_value.backward()

        # шаг градиентного спуска с заданным lr оптимизатора
        optimizer.step()

        # занулить градиент для вычисления его на новой итерации
        optimizer.zero_grad()

        total_loss += loss_value.item()
    
    
    print(f'Эпоха: {epoch + 1}, значение функции потерь: {total_loss/len(train_dl)}')


Эпоха: 1, значение функции потерь: 2.7125170282471234
Эпоха: 2, значение функции потерь: 2.7097522717017632
Эпоха: 3, значение функции потерь: 2.707610679395271
Эпоха: 4, значение функции потерь: 2.706938415378719
Эпоха: 5, значение функции потерь: 2.7061052621701065
Эпоха: 6, значение функции потерь: 2.7058382013659457
Эпоха: 7, значение функции потерь: 2.0224666367103525
Эпоха: 8, значение функции потерь: 0.9832934148899921
Эпоха: 9, значение функции потерь: 0.6376862669145906
Эпоха: 10, значение функции потерь: 0.44920840578806864
Эпоха: 11, значение функции потерь: 0.36004794047121363
Эпоха: 12, значение функции потерь: 0.2889871146707308
Эпоха: 13, значение функции потерь: 0.2263603408486296
Эпоха: 14, значение функции потерь: 0.18770611265198492
Эпоха: 15, значение функции потерь: 0.16541385328905148
Эпоха: 16, значение функции потерь: 0.12939940592136992
Эпоха: 17, значение функции потерь: 0.12411660413173112
Эпоха: 18, значение функции потерь: 0.11610806605161784
Эпоха: 19, зна

YEAY! Как видим результаты не могут не радовать, очень хорошо отработала GRU, **лучше** всех остальных

In [180]:
def evaluate(model):
    '''
    This method is for EVALUATUION purposes.
    Returns: `y_true` and `y_pred`
    '''
    y_true = []

    y_pred = []
    
    with torch.no_grad():
        for x, y in test_dl:
            x, y = x.to('cuda:0'), y.to('cuda:0')
            outputs = model(x)
            _, predicted = torch.max(outputs, 1)
            print(y.cpu().numpy())
            print(predicted.cpu().numpy())
            print('-----------------')
            y_true.extend(y.cpu().numpy())
            y_pred.extend(predicted.cpu().numpy())
            
    return y_true, y_pred

In [178]:
y_true, y_pred = evaluate(gru_model)

[ 0  1  0  1  0  0 14  0  0  1  0  1  0  1  1  1  0  0  5  0  3  0  6  1
  5  0 13  0  0  0  1  5  6  0  1  1  0  0  1  1  0  0  0  7  4  1  0  1
  3  0  0  1  1  0  0  1  0  5  2  0  0  0  4  1]
[ 0  3  0  1  0  0 14  0  0  1  3  1  0  0  1  0  0  3  5  0  1  0  6  1
  5  0 13  0  0  0  1  5  6  0  0 10  0  0  1 13  0  0  0  7  4  1  0  1
  1  0  0  1  1  0  0  1  0  5  2  0  0  0  4  1]
-----------------
[ 0  0  3  1  0  0  1  3 13  1  0  0  0  1  0 11 13  0  1  0  0  0  0  0
  0  0  0  0  6  0  0  0  0  1  0  1  0  0  2 14  1  0  0  0  0  1  0  0
  0  0  0  0  0  0  0  0  1  1  0  0  0  0  0  0]
[ 1  0  0  1  0  1  1  3  1  1  0  0  0  1  0 11  4  0  1  0  7  0  0  0
  0  6  0  0  6  0  0  0  0  1  0  0  0  0  8 14  1  0  3  0  0  7  0  0
  9  0  0  0  0  0  1  0  1  1  0  0  0  0  0  0]
-----------------
[ 0  0  1  0  0  0  0  0  0  0  1  0  0  0  7  1  0  1  0  1  0  0  0  6
  3  1  0  1  0  1  8  0  4  0  5  1  0  1  3 12  0  1  1  0  0 13  0  0
  0  0  0  0  1  0  1  0  0  0  1 

In [181]:
from sklearn.metrics import classification_report
print(classification_report(y_true, y_pred))


              precision    recall  f1-score   support

           0       0.95      0.86      0.90      2124
           1       0.86      0.82      0.84       924
           2       0.82      0.92      0.87       106
           3       0.47      0.72      0.57        96
           4       0.65      0.80      0.72        55
           5       0.86      0.90      0.88       108
           6       0.62      0.84      0.71        81
           7       0.51      0.75      0.61        48
           8       0.33      0.78      0.46        40
           9       0.24      0.56      0.34        16
          10       0.30      0.40      0.34        15
          11       0.65      0.65      0.65        17
          12       0.21      0.79      0.33        14
          13       0.48      0.55      0.51        20
          14       0.76      0.84      0.80        19

    accuracy                           0.84      3683
   macro avg       0.58      0.74      0.63      3683
weighted avg       0.87   